In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.graph_objects as go
import json
import warnings
warnings.filterwarnings("ignore")
import folium
import geopandas as gpd

from scipy.signal import find_peaks, argrelextrema
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.datasets import get_rdataset
from statsmodels.tsa.stattools import adfuller
from folium.plugins import MarkerCluster
from shapely.geometry import Point
from plotly.subplots import make_subplots

##Анализ временных рядов:
***1. Проанализируйте тенденцию создания сделок с течением времени и их связь с звонками.***

In [2]:
deals = pd.read_excel('Deals (Result).xlsx', dtype={'Id': str,
                                                    'Contact Name': str})

In [3]:
calls = pd.read_excel('Calls (Result).xlsx', dtype={'Id': str,
                                                    "CONTACTID": str})

In [4]:
contacts = pd.read_excel('Contacts (Result).xlsx', dtype={'Id': str})

In [5]:
spend = pd.read_excel('Spend (Result).xlsx')

In [6]:
calls.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92617 entries, 0 to 92616
Data columns (total 9 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   Id                          92617 non-null  object        
 1   Call Start Time             92617 non-null  datetime64[ns]
 2   Call Owner Name             92617 non-null  object        
 3   CONTACTID                   92617 non-null  object        
 4   Call Type                   92617 non-null  object        
 5   Call Duration (in seconds)  92538 non-null  float64       
 6   Call Status                 92617 non-null  object        
 7   Outgoing Call Status        92617 non-null  object        
 8   Scheduled in CRM            92617 non-null  object        
dtypes: datetime64[ns](1), float64(1), object(7)
memory usage: 6.4+ MB


In [7]:
deals.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19788 entries, 0 to 19787
Data columns (total 23 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Id                   19788 non-null  object        
 1   Deal Owner Name      19788 non-null  object        
 2   Closing Date         13129 non-null  datetime64[ns]
 3   Quality              17557 non-null  object        
 4   Stage                19788 non-null  object        
 5   Lost Reason          14347 non-null  object        
 6   Page                 19788 non-null  object        
 7   Campaign             15555 non-null  object        
 8   Content              13771 non-null  object        
 9   Term                 12077 non-null  object        
 10  Source               19788 non-null  object        
 11  Payment Type         482 non-null    object        
 12  Product              3537 non-null   object        
 13  Education Type       3390 non-n

In [8]:
contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18510 entries, 0 to 18509
Data columns (total 4 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   Id                  18510 non-null  object        
 1   Contact Owner Name  18510 non-null  object        
 2   Created Time        18510 non-null  datetime64[ns]
 3   Modified Time       18510 non-null  datetime64[ns]
dtypes: datetime64[ns](2), object(2)
memory usage: 578.6+ KB


Для выполнения поставленных задач необходимо объединить таблицы. Определим подходящие для этого поля.

Оптимальные поля для объединения:
- Contact Name (Deals) и Id (Contacts): для связи информации о сделках с контактами.
- CONTACTID (Calls) и Id (Contacts): для связи информации о звонках с контактами.

Для объединения таблиц будем использовать тип left join, чтобы сохранить все данные из основной таблицы и добавить данные из связанной таблицы, где это возможно. Это позволяет сохранить как можно больше информации, даже если некоторые данные отсутствуют.

In [9]:
deals_contacts = pd.merge(deals, contacts, left_on='Contact Name',
                          right_on='Id', how='left')
calls_contacts = pd.merge(calls, contacts, left_on='CONTACTID',
                          right_on='Id', how='left')

In [10]:
deals_contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19788 entries, 0 to 19787
Data columns (total 27 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Id_x                 19788 non-null  object        
 1   Deal Owner Name      19788 non-null  object        
 2   Closing Date         13129 non-null  datetime64[ns]
 3   Quality              17557 non-null  object        
 4   Stage                19788 non-null  object        
 5   Lost Reason          14347 non-null  object        
 6   Page                 19788 non-null  object        
 7   Campaign             15555 non-null  object        
 8   Content              13771 non-null  object        
 9   Term                 12077 non-null  object        
 10  Source               19788 non-null  object        
 11  Payment Type         482 non-null    object        
 12  Product              3537 non-null   object        
 13  Education Type       3390 non-n

In [11]:
calls_contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 92617 entries, 0 to 92616
Data columns (total 13 columns):
 #   Column                      Non-Null Count  Dtype         
---  ------                      --------------  -----         
 0   Id_x                        92617 non-null  object        
 1   Call Start Time             92617 non-null  datetime64[ns]
 2   Call Owner Name             92617 non-null  object        
 3   CONTACTID                   92617 non-null  object        
 4   Call Type                   92617 non-null  object        
 5   Call Duration (in seconds)  92538 non-null  float64       
 6   Call Status                 92617 non-null  object        
 7   Outgoing Call Status        92617 non-null  object        
 8   Scheduled in CRM            92617 non-null  object        
 9   Id_y                        88713 non-null  object        
 10  Contact Owner Name          88713 non-null  object        
 11  Created Time                88713 non-null  datetime64

Агрегирование данных по месяцам для звонков и сделок

In [12]:
deals_by_time = deals_contacts.resample(
            'ME', on='Created Time_y').size().reset_index(name='Deals Count')
calls_by_time = calls_contacts.resample(
            'ME', on='Call Start Time').size().reset_index(name='Calls Count')

Объединяем полученные после агрегирования таблицы

In [13]:
time_series_data = pd.merge(deals_by_time, calls_by_time,
                            left_on='Created Time_y',
                            right_on='Call Start Time',
                            how='outer')
time_series_data.rename(columns={'Created Time_y': 'Date'}, inplace=True)

Создаем визуализацию тенденции создания сделок и звонков по времени

In [14]:
fig = px.line(time_series_data,
              x='Date',
              y=['Deals Count', 'Calls Count'],
              title='Trend of deals and calls over time',
              labels={'value': 'Quantity', 'variable': ''},
              template='plotly_white', markers=True)

for i, column in enumerate(['Deals Count', 'Calls Count']):
    fig.data[i].update(
        text=time_series_data[column],
        textposition="top center",
        mode="lines+markers+text"
    )

fig.update_layout(
    title_x=0.5,
    xaxis_title="",
    legend=dict(
    orientation="h",
    x=0.5,
    xanchor="center",
    y=1.1
    )
)

fig.show()

**ВЫВОД:** На графике видно, что количество звонков и количество сделок имеют разные динамики за рассматриваемый период. Количество звонков демонстрирует значительный рост, достигая пика в мае 2024 года, после чего наблюдается снижение. В то же время, количество сделок также растет, но более плавно, с менее выраженными пиками. Максимальное значение сделок также приходится на май 2024 года, что может указывать на корреляцию между активностью звонков и количеством заключаемых сделок. Общее количество сделок заметно ниже по сравнению с количеством звонков, что подчеркивает значимость эффективности конверсии звонков в успешные сделки.

Для более детального анализа построим временной ряд с интервалом в недели, а затем проведем декомпозицию, чтобы выявить тренды и сезонность.
Построение временного ряда с интервалом в две недели позволяет лучше видеть изменения и тренды в данных, поскольку более мелкий интервал дает более детализированное представление о данных.

In [15]:
deals_by_time_w = deals_contacts.resample(
                'W', on='Created Time_y').size().reset_index(name='Deals Count')
calls_by_time_w = calls_contacts.resample(
            'W', on='Call Start Time').size().reset_index(name='Calls Count')
time_series_data_w = pd.merge(deals_by_time_w, calls_by_time_w,
                             left_on='Created Time_y',
                             right_on='Call Start Time',
                             how='outer')
time_series_data_w = time_series_data_w.rename(
    columns={'Created Time_y': 'Date'})

In [16]:
def find_extrema(series):
    indexes_max = argrelextrema(series.values, np.greater, order=2)[0]
    return indexes_max

fig = px.line(time_series_data_w,
              x='Date',
              y=['Deals Count', 'Calls Count'],
              title='Trend of deals and calls over time',
              labels={'value': 'Quantuty', 'variable': ''},
              template='plotly_white', markers=True)

for i, column in enumerate(['Deals Count', 'Calls Count']):
    indexes_max = find_extrema(time_series_data_w[column].fillna(0))
    text_labels = ['' if idx not in indexes_max else f'{int(val)}'
                   for idx, val in enumerate(time_series_data_w[column])]

    fig.data[i].update(
        text=text_labels,
        textposition="top center",
        mode="lines+markers+text"
    )

    x_vals = np.arange(len(time_series_data_w))
    y_vals = time_series_data_w[column].fillna(0).values
    trend = np.polyfit(x_vals, y_vals, deg=1)
    trend_line = np.polyval(trend, x_vals)

    fig.add_scatter(x=time_series_data_w['Date'], y=trend_line, mode='lines',
                    name=f'{column} Trend', line=dict(dash='dot'))

fig.update_layout(
    title_x=0.5,
    xaxis_title="",
    legend=dict(
    orientation="h",
    x=0.5,
    xanchor="center",
    y=1.1
    )
)

fig.show()

###Общий вывод по двум графикам: :

Глобальный тренд (помесячный анализ) показывает стабильный рост звонков и сделок до мая 2024, затем резкий спад.

Детализированный анализ (понедельный) выявляет цикличность — рост каждые 3-4 недели.

Пики звонков обычно предшествуют пикам сделок, что логично (после звонков идет конверсия в сделки).

Спад после мая 2024 требует дополнительного анализа — возможно, связано с сезоном, изменением маркетинговых активностей или другими факторами.

####Рекомендации:

Проанализировать, что происходило в мае 2024 — была ли маркетинговая кампания, скидки или изменения в бизнес-стратегии.
Изучить цикл 3-4 недель и попробовать его оптимизировать (увеличить количество звонков в периоды спада).
Рассмотреть причины резкого снижения после мая 2024 и возможные решения.

На предыдущих графиках были выявлены общие тренды по сделкам и звонкам, включая их рост и сезонные колебания. Однако для более глубокого анализа факторов, влияющих на динамику сделок и звонков, важно рассмотреть дополнительные переменные, такие как:

* Количество контактов (Contacts Count) – это показатель количества новых потенциальных клиентов. Увеличение контактов может свидетельствовать о росте интереса к продукту.
* Маркетинговые расходы (Ad Spend) – анализ бюджета, выделяемого на привлечение клиентов, и его влияние на сделки и звонки.

In [17]:
def transfer_to_week(df, time_column, target_column=None):
    df_copy = df.copy()
    result = pd.DataFrame()
    if target_column is not None:
      weekly_time_series = df_copy.set_index(time_column)\
      .resample('W')[target_column].sum().reset_index()
      result['Date'] = weekly_time_series[time_column]
      result['Target'] = weekly_time_series[target_column]
    else:
      weekly_time_series = df_copy.set_index(time_column)\
      .resample('W').size().reset_index()
      result['Date'] = weekly_time_series[time_column]
      result['Target'] = weekly_time_series[0]
    return result

In [18]:
spend_w = transfer_to_week(spend,'Date', 'Spend')
contacts_w = transfer_to_week(contacts, 'Created Time')
deals_w = transfer_to_week(deals, 'Created Time')
calls_w = transfer_to_week(calls, 'Call Start Time')

In [19]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=deals_w['Date'],
                         y=deals_w['Target'],
                         mode='lines+markers',
                         name='Deals Count (Weekly)'))

fig.add_trace(go.Scatter(x=calls_w['Date'],
                         y=calls_w['Target'],
                         mode='lines+markers',
                         name='Calls Count (Weekly)'))

fig.add_trace(go.Scatter(x=contacts_w['Date'],
                         y=contacts_w['Target'],
                         mode='lines+markers',
                         name='Contacts Count (Weekly)',
                         line=dict(dash='dash')))

fig.add_trace(go.Scatter(x=spend_w['Date'],
                         y=spend_w['Target'],
                         mode='lines+markers',
                         name='Ad Spend (Weekly)',
                         line=dict(dash='dot')))

fig.update_layout(
    title='Weekly Trends of Deals, Calls, Contacts, and Ad Spend',
    title_x=0.5,
    yaxis_title='Count / Spend',
    legend_title='',
    legend=dict(
        orientation="h",
        x=0.5,
        xanchor="center",
        y=1.1
    ),
    xaxis=dict(tickangle=0),
    template='plotly_white'
)

fig.show()

### Вывод по графику
* Рост сделок и звонков во многом совпадает с ростом маркетинговых расходов

* Видны периоды, когда рост рекламных затрат предшествует увеличению количества звонков и сделок.
Это подтверждает, что маркетинговая активность играет ключевую роль в привлечении клиентов.
Контакты имеют более стабильный, но незначительный рост

* Количество новых контактов увеличивается, но не так резко, как звонки и сделки.
Возможно, на рынок уже вышли наиболее заинтересованные клиенты, и эффективность привлечения новых контактов начинает снижаться.
Наблюдается цикличность в маркетинговых расходах и их влияние на остальные показатели

* Каждые несколько недель можно увидеть пики рекламных затрат, за которыми следуют пики звонков и сделок.
Это говорит о том, что маркетинговая стратегия работает, но требует анализа эффективности расходов.
Спад после мая 2024 подтверждается и на этом графике

* После майского пика происходит резкое снижение всех метрик, включая звонки, сделки и рекламные затраты.
Важно выяснить, что стало причиной — возможно, изменение стратегии, сезонные факторы или перераспределение бюджета.

In [20]:
time_series_data_cleaned_w = time_series_data_w.dropna(subset=['Deals Count'])

In [21]:
decomposition_deals = seasonal_decompose(
    time_series_data_cleaned_w['Deals Count'],
    model='multiplicative', period=12)

trend_deals = decomposition_deals.trend
seasonal_deals = decomposition_deals.seasonal
residual_deals = decomposition_deals.resid

In [22]:
if 'Calls Count' in time_series_data_cleaned_w.columns:
    decomposition_calls = seasonal_decompose(
        time_series_data_cleaned_w['Calls Count'],
        model='multiplicative',
        period=12
    )
    trend_calls = decomposition_calls.trend
    seasonal_calls = decomposition_calls.seasonal
    residual_calls = decomposition_calls.resid
else:
    trend_calls, seasonal_calls, residual_calls = None, None, None

In [23]:
def plot_series_subplot(fig, series, title, color, row, col):
    if series is not None:
        fig.add_trace(
            go.Scatter(
                x=time_series_data_cleaned_w.index,
                y=series, mode="lines", name=title, line=dict(color=color)),
            row=row,
            col=col,
        )

fig = make_subplots(rows=3, cols=2, subplot_titles=(
    "Trend - Deals Count", "Trend - Calls Count",
    "Seasonality - Deals Count", "Seasonality - Calls Count",
    "Residuals - Deals Count", "Residuals - Calls Count"
))

plot_series_subplot(fig, trend_deals, "Trend - Deals Count", "blue", 1, 1)
plot_series_subplot(fig, trend_calls, "Trend - Calls Count", "green", 1, 2)

plot_series_subplot(fig, seasonal_deals,
                    "Seasonality - Deals Count", "blue", 2, 1)
plot_series_subplot(fig, seasonal_calls,
                    "Seasonality - Calls Count", "green", 2, 2)

plot_series_subplot(fig, residual_deals,
                    "Residuals - Deals Count", "blue", 3, 1)
plot_series_subplot(fig, residual_calls,
                    "Residuals - Calls Count", "green", 3, 2)

fig.update_layout(height=900, width=1200, showlegend=False)
fig.show()

fig_initial = make_subplots(rows=1, cols=2, subplot_titles=(
    "Initial Data - Deals Count", "Initial Data - Calls Count"
))

plot_series_subplot(fig_initial, time_series_data_cleaned_w["Deals Count"],
                    "Initial Data - Deals Count", "blue", 1, 1)
if "Calls Count" in time_series_data_cleaned_w.columns:
    plot_series_subplot(fig_initial, time_series_data_cleaned_w["Calls Count"],
                        "Initial Data - Calls Count", "green", 1, 2)

fig_initial.update_layout(height=400, width=1200, showlegend=False)
fig_initial.show()

**ВЫВОДЫ:**

**Общий тренд (Trend):**
- Для звонков наблюдается положительный тренд, что говорит о росте количества звонков с течением времени. Это может свидетельствовать об увеличении активности клиентов или усилении маркетинговых усилий.
- Для сделок также наблюдается положительный тренд, однако он менее выражен, что может указывать на более стабильный рост по сравнению с количеством звонков.

**Сезонность (Seasonality):**
- Оба временных ряда показывают наличие выраженной сезонности с периодическими колебаниями каждые две недели. Это может быть связано с регулярными маркетинговыми кампаниями, акциями или другими факторами, влияющими на поведение клиентов.
- Поскольку сезонные колебания есть, можно предложить планировать маркетинговые кампании с учетом выявленных циклов для максимального охвата целевой аудитории.
  
**Остатки (Residuality):**
- Остатки показывают случайные колебания, которые не объясняются трендом или сезонностью. Временные ряды остаточных компонентов для звонков и сделок указывают на наличие нерегулярных событий, которые могут влиять на количество звонков и сделок.
- Рассмотрение факторов, которые могут влиять на случайные колебания, поможет снизить их влияние и повысить стабильность показателей.

**Исходные данные (Initial Data):**
* На графиках видно, что количество звонков и количество сделок имеют схожий тренд роста, однако количество звонков растет более резко и достигает значительно более высоких значений. Это подтверждает, что конверсия звонков в сделки не является стабильной и может требовать оптимизации. Также наблюдаются колебания в количестве сделок, что может быть связано с сезонностью или изменениями в стратегии продаж.

***2. Изучите распределение времени закрытия сделок и продолжительность периода от создания до закрытия.***

In [24]:
min_date = deals_contacts['Closing Date'].min()
max_date = deals_contacts['Closing Date'].max()
print(min_date, max_date)

2022-10-11 00:00:00 2024-12-11 00:00:00


In [25]:
min_date1 = deals['Created Time'].min()
max_date1 = deals['Created Time'].max()
print(min_date1, max_date1)

2023-07-03 17:03:00 2024-06-21 15:30:00


In [26]:
fig = px.box(deals_contacts, x='Closing Date', title='Closing Date')

fig.update_layout(
    xaxis_title="Closing Date Outliers",
    yaxis_title="",
    showlegend=False,
    template="plotly_white"
)

fig.show()

In [27]:
deals_contacts = deals_contacts[deals_contacts['Closing Date'] >= min_date1]

In [28]:
fig = px.box(deals_contacts, x='Closing Date', title='Closing Date')

fig.update_layout(
    xaxis_title="Closing Date Outliers",
    yaxis_title="",
    showlegend=False,
    template="plotly_white"
)

fig.show()

На основании построенного boxplot и расчетов минимального и максимального значения для Closing Date и Created Time мы берем интервал, исключая точечные выбросы, для построения графика распределение времени закрытия сделок и продолжительность периода от создания до закрытия, с 01.07.2023 по 01.10.2024

In [29]:
deals_contacts['Duration'] = abs((deals_contacts['Closing Date']\
                                  - deals_contacts['Created Time_y']).dt.days)

In [30]:
fig = px.histogram(deals_contacts, x='Duration', title='Duration', nbins=30)

fig.update_layout(
    xaxis_title="Duration",
    yaxis_title="Count",
    showlegend=False,
    template="plotly_white"
)

fig.show()

In [31]:
Q1 = deals_contacts['Duration'].quantile(0.25)
Q3 = deals_contacts['Duration'].quantile(0.75)
IQR = Q3 - Q1

lower_whisker = Q1 - 1.5 * IQR
upper_whisker = Q3 + 1.5 * IQR

outliers = deals_contacts[(deals_contacts['Duration'] < lower_whisker) |
                          (deals_contacts['Duration'] > upper_whisker)]
num_outliers = len(outliers)

total_points = len(deals_contacts)

outlier_percentage = (num_outliers / total_points) * 100

print(f"Количество выбросов: {num_outliers} из {total_points} записей")
print(f"Процент выбросов: {outlier_percentage:.2f}%")

Количество выбросов: 1955 из 13127 записей
Процент выбросов: 14.89%


In [32]:
deals_contacts_filtered = deals_contacts[
    (deals_contacts["Duration"] >= lower_whisker)
    & (deals_contacts["Duration"] <= upper_whisker)
]

fig = make_subplots(
    rows=1,
    cols=2,
    subplot_titles=[
        "Distribution of Deal Closing Dates",
        "Distribution of Deal Durations",
    ],
)

fig.add_trace(
    go.Histogram(
        x=deals_contacts_filtered["Closing Date"],
        nbinsx=30,
        marker_color="skyblue",
        name="Closing Date",
    ),
    row=1,
    col=1,
)

fig.add_trace(
    go.Histogram(
        x=deals_contacts_filtered["Duration"],
        nbinsx=30,
        marker_color="salmon",
        name="Duration",
    ),
    row=1,
    col=2,
)

closing_date_min = deals_contacts_filtered["Closing Date"].min()
closing_date_max = deals_contacts_filtered["Closing Date"].max()
duration_min = deals_contacts_filtered["Duration"].min()
duration_max = deals_contacts_filtered["Duration"].max()

fig.update_xaxes(
    range=[closing_date_min - pd.Timedelta(days=10),
           closing_date_max + pd.Timedelta(days=10)],
    row=1,
    col=1,
)
fig.update_xaxes(range=[duration_min - 2, duration_max + 2], row=1, col=2)

fig.update_layout(
    height=500,
    bargap=0.1,
    showlegend=False,
)

fig.update_xaxes(title_text="Closing Date", row=1, col=1)
fig.update_yaxes(title_text="Number of Deals", row=1, col=1)

fig.update_xaxes(title_text="Duration (days)", row=1, col=2)
fig.update_yaxes(title_text="Number of Deals", row=1, col=2)

fig.show()

####ВЫВОД:

График распределения дат закрытия сделок показывает, что количество закрытых сделок увеличивается с начала 2024 года, достигая пиков в феврале и апреле 2024 года. В другие месяцы количество закрытых сделок более равномерно распределено, но с меньшим числом сделок в каждом месяце. Это может указывать на сезонные колебания или влияния определенных факторов в эти периоды, которые способствуют увеличению закрытых сделок.

Распределение продолжительности периодов от создания до закрытия сделки показывает, что большинство сделок закрываются в течение первых 10 дней после их создания, что свидетельствует о высокой эффективности процесса продаж. Однако, есть несколько сделок, которые закрываются спустя более длительные периоды, вплоть до 140 дней, хотя такие случаи редки. Основная масса сделок закрывается относительно быстро, что говорит об эффективных процессах работы с клиентами, но длительные периоды закрытия некоторых сделок требуют дополнительного анализа для улучшения этих процессов.

##Анализ эффективности кампаний:
***1. Сравните эффективность различных кампаний с точки зрения генерации лидов и коэффициента конверсии.***


In [33]:
spend[['Campaign', 'Source']] = spend[['Campaign', 'Source']].astype('category')

In [34]:
deals_spend = pd.merge(deals, spend, on='Campaign', how='outer')

In [35]:
deals_spend.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9533117 entries, 0 to 9533116
Data columns (total 30 columns):
 #   Column               Dtype         
---  ------               -----         
 0   Id                   object        
 1   Deal Owner Name      object        
 2   Closing Date         datetime64[ns]
 3   Quality              object        
 4   Stage                object        
 5   Lost Reason          object        
 6   Page                 object        
 7   Campaign             object        
 8   Content              object        
 9   Term                 object        
 10  Source_x             object        
 11  Payment Type         object        
 12  Product              object        
 13  Education Type       object        
 14  Created Time         datetime64[ns]
 15  Course duration      float64       
 16  Months of study      float64       
 17  Initial Amount Paid  float64       
 18  Offer Total Amount   float64       
 19  Contact Name         

In [36]:
deals_spend['Campaign'] = deals_spend['Campaign'].astype('category')

In [37]:
deals_spend.head()

Id Deal Owner Name Closing Date Quality Stage Lost Reason Page  \
0  NaN             NaN          NaT     NaN   NaN         NaN  NaN   
1  NaN             NaN          NaT     NaN   NaN         NaN  NaN   
2  NaN             NaN          NaT     NaN   NaN         NaN  NaN   
3  NaN             NaN          NaT     NaN   NaN         NaN  NaN   
4  NaN             NaN          NaT     NaN   NaN         NaN  NaN   

                  Campaign Content Term  ... City Level of Deutsch  \
0  01.02.24wide_webinar_DE     NaN  NaN  ...  NaN              NaN   
1  01.02.24wide_webinar_DE     NaN  NaN  ...  NaN              NaN   
2  01.02.24wide_webinar_DE     NaN  NaN  ...  NaN              NaN   
3  01.02.24wide_webinar_DE     NaN  NaN  ...  NaN              NaN   
4  01.02.24wide_webinar_DE     NaN  NaN  ...  NaN              NaN   

  SLA Seconds       Date Source_y  Impressions  Spend  Clicks  AdGroup  \
0         NaN 2024-02-03  Webinar       2927.0  33.14    24.0     wide   
1         NaN 2024-02-03  Webinar        771.0   6.40     4.0     wide   
2         NaN 2024-02-04  Webinar       3076.0  33.78    33.0     wide   
3         NaN 2024-02-04  Webinar        182.0   1.52     2.0     wide   
4         NaN 2024-02-05  Webinar        801.0   7.72    10.0     wide   

          Ad  
0  v1webinar  
1  v2webinar  
2  v1webinar  
3  v2webinar  
4  v2webinar  

[5 rows x 30 columns]

In [38]:
deals_spend['Source_y'].value_counts()

Source_y
Facebook Ads      4577580
Tiktok Ads        2799887
Youtube Ads       1947599
Google Ads         152861
Webinar             41230
Test                 2668
Telegram posts        468
Bloggers              258
Organic               230
SMM                   175
CRM                    78
Partnership            14
Offline                 7
Radio                   1
Name: count, dtype: int64

In [39]:
source_leads = deals_spend[deals_spend['Source_y'] != 'Test'].groupby(
              'Source_y', observed=True).size().reset_index(name='Leads')
source_leads

Source_y    Leads
0         Bloggers      258
1              CRM       78
2     Facebook Ads  4577580
3       Google Ads   152861
4          Offline        7
5          Organic      230
6      Partnership       14
7            Radio        1
8              SMM      175
9   Telegram posts      468
10      Tiktok Ads  2799887
11         Webinar    41230
12     Youtube Ads  1947599

In [40]:
successful_deals = deals_spend[(deals_spend['Source_y'] != 'Test')
& (deals_spend['Stage'] == 'Payment Done')
].groupby('Source_y', observed=True).size().reset_index(name='Successful Deals')
successful_deals

Source_y  Successful Deals
0  Facebook Ads            230271
1    Google Ads              3682
2    Tiktok Ads             87765
3       Webinar               533
4   Youtube Ads             64607

In [41]:
source_performance = pd.merge(source_leads, successful_deals, on='Source_y',
                              how='outer')

source_performance['Successful Deals'] = source_performance['Successful Deals']\
                                        .fillna(0)
source_performance['Conversion Rate'] = source_performance['Successful Deals']\
                                        / source_performance['Leads'] * 100
source_performance

Source_y    Leads  Successful Deals  Conversion Rate
0         Bloggers      258               0.0         0.000000
1              CRM       78               0.0         0.000000
2     Facebook Ads  4577580          230271.0         5.030409
3       Google Ads   152861            3682.0         2.408724
4          Offline        7               0.0         0.000000
5          Organic      230               0.0         0.000000
6      Partnership       14               0.0         0.000000
7            Radio        1               0.0         0.000000
8              SMM      175               0.0         0.000000
9   Telegram posts      468               0.0         0.000000
10      Tiktok Ads  2799887           87765.0         3.134591
11         Webinar    41230             533.0         1.292748
12     Youtube Ads  1947599           64607.0         3.317264

In [42]:
fig = go.Figure()

source_performance = source_performance.sort_values(
    by='Leads', ascending=False
)

fig.add_trace(go.Bar(
    x=source_performance['Source_y'],
    y=source_performance['Leads'],
    name='Leads',
    marker_color='skyblue',
    text=source_performance['Leads'],
    textposition='outside'
))

fig.add_trace(go.Scatter(
    x=source_performance['Source_y'],
    y=source_performance['Conversion Rate'],
    name='Conversion Rate (%)',
    mode='lines+markers+text',
    text=[f"{y:.1f}%" for y in source_performance['Conversion Rate']],
    textposition='top center',
    marker=dict(color='red', size=8),
    line=dict(color='red', width=2, dash='solid'),
    yaxis='y2'
))


fig.update_layout(
    title=dict(
        text="Source Performance: Leads and Conversion Rate",
        x=0.5,
        xanchor="center",
        font=dict(size=18)
    ),
    xaxis=dict(title="Source", tickangle=-45),
    yaxis=dict(title="Number of Leads", showgrid=False),
    yaxis2=dict(
        title="Conversion Rate (%)",
        overlaying='y',
        side='right',
        showgrid=False,
        range=[-1, 20]
    ),
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=1,
        xanchor="center",
        x=0.5
    ),
    height=800,
    width=1200,
    template="plotly_white"
)

fig.show()

### **Выводы по графику:**
1. Наибольшее количество лидов приходит с Facebook Ads (4,57M), TikTok Ads (2,79M) и YouTube Ads (1,95M).  
2. Конверсия выше всего у Facebook Ads (5,0%), YouTube Ads (3,3%) и TikTok Ads (3,1%).  
3. Google Ads (152K лидов) имеет низкую конверсию (2,4%), что ниже топ-3 источников.  
4. Остальные источники приносят мало лидов, а Telegram, Bloggers, Organic, SMM, CRM, Partnership, Offline и Radio показывают 0% конверсии.  
 **Вывод:** Стоит сосредоточиться на Facebook, TikTok и YouTube Ads как на наиболее эффективных каналах привлечения.

2. ***Оцените эффективность различных маркетинговых источников (Source) в генерировании качественных лидов.***


Для более детального анализа построим тепловую карту по маркетинговым каналам с учетом 4 метрик, чтобы проанализировать корреляцию между этими метриками:
* количество кликов
* затраты на рекламу
* общая сумма продаж
* количество успешных сделок






In [43]:
filtered_sources = [
    "Facebook Ads", "Tiktok Ads", "Youtube Ads", "Google Ads", "Webinar"
                   ]
filtered_deals = deals_spend[deals_spend['Source_y']\
                             .astype(str).isin(filtered_sources)]

In [44]:
filtered_deals['Source_y'].value_counts()

Source_y
Facebook Ads      4577580
Tiktok Ads        2799887
Youtube Ads       1947599
Google Ads         152861
Webinar             41230
Bloggers                0
CRM                     0
Offline                 0
Organic                 0
Partnership             0
Radio                   0
SMM                     0
Telegram posts          0
Test                    0
Name: count, dtype: int64

In [45]:
print(deals_spend['Source_y'].unique())

['Webinar', 'Facebook Ads', 'Test', 'Tiktok Ads', NaN, ..., 'CRM', 'Offline', 'Partnership', 'Radio', 'Youtube Ads']
Length: 15
Categories (14, object): ['Bloggers', 'CRM', 'Facebook Ads', 'Google Ads', ..., 'Test', 'Tiktok Ads',
                          'Webinar', 'Youtube Ads']


In [46]:
print(deals_spend['Source_y'].dtype)

category


In [47]:
deals_spend['Source_y'].isna().sum()

10061

In [48]:
filtered_df = deals_spend[deals_spend['Source_y'].isin(filtered_sources)]

heatmap_data = filtered_df.groupby('Source_y', observed=False).agg({
    'Clicks': 'sum',
    'Spend': 'sum',
    'Offer Total Amount': 'sum',
    'Stage': lambda x: (x == 'Payment Done').sum()
}).rename(columns={'Stage': 'Successful Deals'}).reset_index()

heatmap_data = heatmap_data[heatmap_data['Source_y'].isin(filtered_sources)]

cols = ['Clicks', 'Spend', 'Offer Total Amount', 'Successful Deals']
heatmap_data[cols] = heatmap_data[cols].astype(float)

heatmap_data.set_index('Source_y', inplace=True)
heatmap_data_normalized = heatmap_data / heatmap_data.max()

fig = px.imshow(
    heatmap_data_normalized,
    labels=dict(x="Metrics", y="Source", color="Normalized Value"),
    x=heatmap_data_normalized.columns,
    y=heatmap_data_normalized.index,
    color_continuous_scale="PuBu",
    text_auto=".2f"
)

fig.update_layout(
    title=dict(
        text="Heatmap: Clicks, Spend, Revenue, and Successful Deals by Source",
        x=0.465,
        xanchor="center"
    ),
    xaxis_title="Metrics",
    yaxis_title="Source",
    width=1200,
    height=800,
    xaxis=dict(tickangle=0)
)

fig.show()

#Выводы
На основании проведенного анализа можно сделать следующие выводы.
1. **Facebook Ads**  
   - Высокая корреляция между Spend (0.80) и Clicks (0.30).  
   - Полная (1.00) корреляция между Offer Total Amount и Successful Deals.  
   - Это указывает на то, что все потраченные деньги напрямую конвертируются в выручку и успешные сделки.  

2. **Google Ads**  
   - Умеренная корреляция между Clicks (0.53) и Spend (0.49).  
   - Практически отсутствует связь с Offer Total Amount (0.02) и Successful Deals (0.02).  
   - Это может указывать на то, что Google Ads генерирует клики, но они не приводят к значительным доходам или сделкам.  

3. **Tiktok Ads**  
   - Средняя корреляция Clicks (0.38) и Spend (0.65).  
   - Умеренная корреляция Offer Total Amount (0.44) и Successful Deals (0.38).  
   - Указывает на то, что TikTok даёт умеренные результаты как по привлечению клиентов, так и по выручке.  

4. **Webinar**  
   - Практически нулевая корреляция со всеми метриками.  
   - Это говорит о том, что вебинары не приносят значительного трафика, расходов, доходов или успешных сделок.  

5. **Youtube Ads**  
   - Clicks (1.00) и Spend (1.00)* → идеальная зависимость (логично, так как без бюджета нет кликов).  
   - Низкая корреляция с Offer Total Amount (0.29) и Successful Deals (0.28).  
   - Это означает, что YouTube приносит трафик, но не всегда приводит к успешным сделкам.  

###  **Рекомендации:**
 **Facebook Ads** — самый эффективный источник, так как инвестиции напрямую связаны с выручкой и успешными сделками. Стоит увеличить бюджет.  

 **Google Ads и YouTube Ads** — создают клики, но не приводят к сделкам. Требуется анализ качества трафика. Возможно, нужно менять таргетинг или креативы.  

 **TikTok Ads** — средний результат, можно протестировать A/B-тесты, чтобы понять, как увеличить выручку.  

 **Webinar** — абсолютно неэффективен. Нужно либо отказаться, либо изменить стратегию проведения вебинаров.  

##Анализ эффективности работы отдела продаж:
***1. Оцените эффективность отдельных владельцев сделок и рекламных кампаний с точки зрения количества обработанных сделок, коэффициента конверсии и общей суммы продаж.***


Проанализируем эффективность отдельных владельцев сделок с точки зрения количества обработанных сделок, коэффициента конверсии и общей суммы продаж (статус Payment Done)

Создадим таблицу, включающую столбцы "Deal Owner Name", "Total Deals", "Successful Deals", "Offer Total Amount" и "Conversion Rate", а тажке посмотрим эти данные на графиках, что поможет достичь нам следующих целей:

- Проанализировать количество обработанных сделок и понять, сколько сделок было обработано каждым владельцем, чтобы оценить их рабочую нагрузку и продуктивность.

- Проанализировать количество успешных сделок (статус "Payment Done"), чтобы оценить, насколько эффективны владельцы в закрытии сделок.

- Проанализировать общую сумму продаж - это общая сумма предложений, которые были успешно закрыты. Таким образом мы можем измерить финансовый вклад каждого владельца в общие продажи.

- Проанализировать коэффициент конверсии, который показывает процент успешных сделок относительно общего числа обработанных сделок, что позволяет оценить эффективность работы владельца сделок.

 Расчет показателей эффективности владельцев сделок
(Считаем количество обработанных, успешных сделок и сумму оплат)

In [49]:
owner_deals = deals.groupby('Deal Owner Name', observed=True)['Id']\
                            .nunique().reset_index(name='Total Deals')

successful_owner_deals = (
    deals[deals['Stage'] == 'Payment Done']
    .groupby('Deal Owner Name', observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals')
)

total_sales = (
    deals[deals['Stage'] == 'Payment Done']
    .groupby('Deal Owner Name', observed=True)['Offer Total Amount']
    .sum().reset_index()
)

Объединение данных и расчет конверсии
(Объединяем таблицы, заполняем пропуски, считаем конверсию и форматируем вывод)

In [50]:
owner_performance = pd.merge(owner_deals, successful_owner_deals,
                             on='Deal Owner Name', how='left')
owner_performance = pd.merge(owner_performance, total_sales,
                             on='Deal Owner Name', how='left')

owner_performance['Successful Deals'] = owner_performance[
                                        'Successful Deals'].fillna(0)
owner_performance['Offer Total Amount'] = owner_performance[
                                        'Offer Total Amount'].fillna(0)
owner_performance['Conversion Rate'] = owner_performance[
                  'Successful Deals'] / owner_performance['Total Deals'] * 100

owner_performance_sorted = owner_performance.sort_values(
                                        by='Successful Deals', ascending=False)

owner_performance_sorted.columns = [
                        'Deal Owner Name', 'Total Deals', 'Successful Deals',
                        'Offer Total Amount', 'Conversion Rate']

formatted_owner_performance_sorted = owner_performance_sorted[
    ['Deal Owner Name', 'Total Deals', 'Successful Deals',
     'Offer Total Amount', 'Conversion Rate']].style.format({
    'Successful Deals': '{:,.0f}',
    'Offer Total Amount': '{:,.0f}',
    'Conversion Rate': '{:.2f}'
}).hide(axis='index')

display(formatted_owner_performance_sorted)

Отсортируем владельцев сделок, исключив тех, у кого мало сделок. (Сортировка по 25 квартилю)

In [51]:
Q1_T = owner_performance['Total Deals'].quantile(0.25)
owner_performance_f_deals = owner_performance[
    owner_performance['Total Deals'] > Q1]

owner_performance_f_deals = owner_performance_f_deals[
    owner_performance_f_deals['Successful Deals'] > 0]

Q1_S = owner_performance_f_deals['Successful Deals'].quantile(0.25)
owner_performance_f_deals = owner_performance_f_deals[
    owner_performance_f_deals['Successful Deals'] > Q1_S]

owner_performance_f_deals_conversion = owner_performance_f_deals.\
sort_values(by='Conversion Rate', ascending=False)

owner_performance_f_deals_conversion

Deal Owner Name  Total Deals  Successful Deals  Offer Total Amount  \
16    Oliver Taylor          160              50.0            524500.0   
13     Kevin Parker          500              40.0            211900.0   
21    Ulysses Adams         2069             141.0           1011400.0   
5     Charlie Davis         2797             148.0           1066600.0   
17  Paula Underwood         1771              93.0            694000.0   
12     Julia Nelson         2085              92.0            718701.0   
7          Eva Kent          452              18.0            132500.0   
15       Nina Scott         1217              46.0            315000.0   
22    Victor Barnes         1187              44.0            356000.0   
18   Quincy Vincent         1805              65.0            465500.0   
2          Ben Hall         1303              46.0            345500.0   
10       Jane Smith          904              31.0            215500.0   
4      Cara Iverson         1033              26.0            215500.0   

    Conversion Rate  
16        31.250000  
13         8.000000  
21         6.814886  
5          5.291384  
17         5.251270  
12         4.412470  
7          3.982301  
15         3.779786  
22         3.706824  
18         3.601108  
2          3.530315  
10         3.429204  
4          2.516941

### Выводы на основе таблицы эффективности менеджеров

1. Лучший показатель конверсии у Oliver Taylor (31.25%)

    * Он закрыл 50 успешных сделок из 160 попыток, что делает его лидером по эффективности.
    * Возможно, работает с более качественными лидами или имеет хорошую технику продаж.

2. Самое большое количество сделок у Charlie Davis (2797 сделок, 148 успешных)

    * Однако его конверсия (5.29%) относительно низкая, что может указывать на работу с менее качественными лидами или слабую стратегию доведения до закрытия сделки.

3. Наибольший доход от успешных сделок у Ulysses Adams (1 011 400€)

    * Он закрыл 141 сделки из 2069 попыток (конверсия 6.81%).
    * Это означает, что он работает с более дорогими предложениями, но не всегда доводит сделки до оплаты.

4. Низкая конверсия у ряда менеджеров, несмотря на высокий объем сделок

    * Например, Kevin Parker обработал 500 сделок, но закрыл только 40, что дало конверсию 8%.
    * Quincy Vincent обработал 1805 сделок, но закрыл только 65 (3.6% конверсия).

5. Jane Smith и Cara Iverson имеют низкие показатели успешных сделок и конверсии

    * У Jane Smith 904 сделки, но только 31 успешная (3.43%).
    * У Cara Iverson 1033 сделки, но всего 26 успешных (2.52%) — самая низкая конверсия среди представленных менеджеров.

###Рекомендации

* Разобраться, почему у Oliver Taylor такая высокая конверсия – возможно, его методы продаж можно адаптировать для других менеджеров.

* Обратить внимание на эффективность работы Charlie Davis и Ulysses Adams – они ведут большое количество сделок, но можно улучшить их конверсию.

* Доработать стратегию работы менеджеров с низкой конверсией (Cara Iverson, Jane Smith) – либо они получают некачественные лиды, либо нуждаются в дополнительном обучении.

Oliver Taylor показал невероятно высокую конверсию. Давайте разберемся в причинах такого успеха.

In [52]:
owner_performance_sorted_conversion = owner_performance.sort_values(
                    by='Conversion Rate', ascending=False)

owner_performance_sorted_conversion.head()

Deal Owner Name  Total Deals  Successful Deals  Offer Total Amount  \
16   Oliver Taylor          160              50.0            524500.0   
11        John Doe           12               1.0                 0.0   
13    Kevin Parker          500              40.0            211900.0   
21   Ulysses Adams         2069             141.0           1011400.0   
5    Charlie Davis         2797             148.0           1066600.0   

    Conversion Rate  
16        31.250000  
11         8.333333  
13         8.000000  
21         6.814886  
5          5.291384

####Анализ высокой конверсии у Oliver Taylor
Конверсия (успешные сделки / общее количество сделок):

* Oliver Taylor: 31.25% (50 успешных сделок из 160)
* Средняя конверсия среди всех сотрудников: 3.68%
* Следующий по конверсии — John Doe с 8.33%, что в почти 4 раза ниже, чем у Oliver Taylor.
* Oliver Taylor резко выделяется среди других сотрудников — его конверсия почти в 9 раз выше средней.

Возможные причины:
* Качество лидов

Возможно, Oliver получает лучшую базу клиентов.
* Больше прогретых клиентов

Если Oliver получает больше контактов, с которыми уже работали, это может влиять на конверсию.
*  Больше/лучше звонков

Возможно, у Oliver Taylor больше звонков или они проходят эффективнее.
* Связь с рекламными кампаниями

Возможно, его сделки связаны с более эффективными рекламными источниками.
Проверим, какие Campaign чаще встречаются в его сделках.

In [53]:
contacts.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18510 entries, 0 to 18509
Data columns (total 4 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   Id                  18510 non-null  object        
 1   Contact Owner Name  18510 non-null  object        
 2   Created Time        18510 non-null  datetime64[ns]
 3   Modified Time       18510 non-null  datetime64[ns]
dtypes: datetime64[ns](2), object(2)
memory usage: 578.6+ KB


In [54]:
oliver_deals = deals[deals['Deal Owner Name'] == 'Oliver Taylor']

oliver_quality_distribution = oliver_deals['Quality'
                              ].value_counts(normalize=True) * 100

oliver_contacts = contacts[contacts['Contact Owner Name'] == 'Oliver Taylor']
total_contacts = oliver_contacts.shape[0]

oliver_calls = calls[calls['Call Owner Name'] == 'Oliver Taylor']
total_calls = oliver_calls.shape[0]
call_status_distribution = oliver_calls['Call Status'
                           ].value_counts(normalize=True) * 100

oliver_campaigns = oliver_deals['Campaign'].value_counts(normalize=True) * 100

print(oliver_quality_distribution, total_contacts,
      total_calls,call_status_distribution, oliver_campaigns)

Quality
B - Medium           44.936709
C - Low              36.075949
A - High             12.658228
D - Non Target        5.696203
E - Non Qualified     0.632911
Name: proportion, dtype: float64 19 10 Call Status
Attended Dialled      90.0
Unattended Dialled    10.0
Name: proportion, dtype: float64 Campaign
Dis_DE                               13.675214
performancemax_digitalmarkt_ru_DE    11.965812
02.07.23wide_DE                       9.401709
youtube_shorts_DE                     9.401709
03.07.23women                         8.547009
24.09.23retargeting_DE                5.982906
12.07.2023wide_DE                     5.128205
07.07.23LAL_DE                        4.273504
12.09.23interests_Uxui_DE             4.273504
mu_DE                                 3.418803
15.07.23b_DE                          2.564103
05.07.23interests_DE                  1.709402
arina_DE                              1.709402
18.10.23wide_gos_DE                   1.709402
Trigger_DE                      

Причины высокой конверсии у Oliver Taylor
* Качество лидов у Oliver выше среднего

81% сделок у Oliver — это клиенты категории B - Medium (44.9%) и C - Low (36.1%).
Категория A - High (12.7%) также выше, чем у большинства сотрудников.
Почти нет нецелевых лидов (D - Non Target = 5.7%, E - Non Qualified = 0.6%).

  Вывод:
* Oliver получает качественную клиентскую базу, в отличие от других.
* Oliver ведет очень мало контактов (всего 19)

У остальных сотрудников контактов намного больше, но их конверсия ниже.
Это может говорить о качественном отборе его клиентов или меньшей нагрузке.
* У него мало звонков (10), но они очень результативные

90% звонков → Attended Dialled (ответили).
Только 10% звонков не отвечены.
Средний показатель по отделу гораздо ниже (~50-60% успешных звонков).

 Вывод:
* Oliver звонит реже, но его клиенты почти всегда отвечают, что повышает шансы на сделку.
* Рекламные кампании, которые приводят клиентов Oliver, очень эффективны

Топ-3 источника:

Dis_DE (13.7%)

performancemax_digitalmarkt_ru_DE (12%)

02.07.23wide_DE (9.4%)

Эти кампании, вероятно, дают лучшую целевую аудиторию, что повышает конверсию.
У других сотрудников доминируют менее эффективные кампании.

 Вывод:
* Oliver работает с наиболее конверсионными кампаниями, что дает качественные лиды.

###Финальный вывод по Oliver Taylor:
* Oliver получает лучших клиентов (высокая доля B и A)
* Ему передают меньше, но качественных контактов (19 контактов)
* Практически все его звонки успешные (90% ответов)
* Он получает лиды из самых результативных рекламных кампаний

Возможное объяснение:
Oliver фокусируется на качестве, а не количестве — ему передают уже прогретых клиентов, он тратит меньше времени на холодные звонки, но проводит их эффективнее.

Если нужен более глубокий анализ, можно посмотреть:

Сколько контактов другим сотрудникам передавалось по тем же рекламным кампаниям.
Были ли у Oliver особенные стратегии продаж (например, скрипты или скидки)

Проанализируем эффективность работы отдела продаж в разрезе рекламных кампаний  с точки зрения количества обработанных сделок, коэффициента конверсии и общей суммы продаж.


In [55]:
campaign_deals = deals[deals['Campaign'] != 'Unknown'].groupby(
    'Campaign', observed=True)['Id'].nunique().reset_index(name='Total Deals')

successful_campaign_deals = deals[(deals['Stage'] == 'Payment Done') &
                            (deals['Campaign'] != 'Unknown')]\
                            .groupby('Campaign', observed=True)['Id']\
                            .nunique().reset_index(name='Successful Deals')

total_sales_campaign = deals[(deals['Stage'] == 'Payment Done') &
                             (deals['Campaign'] != 'Unknown')]\
                    .groupby('Campaign', observed=True)['Offer Total Amount']\
                    .sum().reset_index()

campaign_performance = pd.merge(campaign_deals,
                                successful_campaign_deals,
                                on='Campaign',
                                how='left')
campaign_performance = pd.merge(campaign_performance,
                                total_sales_campaign,
                                on='Campaign',
                                how='left')


campaign_performance['Successful Deals'] = campaign_performance[
    'Successful Deals'].fillna(0)
campaign_performance['Offer Total Amount'] = campaign_performance[
    'Offer Total Amount'].fillna(0)
campaign_performance['Conversion Rate'] = campaign_performance[
    'Successful Deals'] / campaign_performance['Total Deals'] * 100

campaign_performance_sorted = campaign_performance.sort_values(
    by='Successful Deals', ascending=False)

campaign_performance_sorted.columns = [
                                'Campaign', 'Total Deals', 'Successful Deals',
                                'Offer Total Amount', 'Conversion Rate']

formatted_campaign_performance_sorted = campaign_performance_sorted[
    ['Campaign', 'Total Deals', 'Successful Deals',
     'Offer Total Amount', 'Conversion Rate']].style.format({
    'Successful Deals': '{:,.0f}',
    'Offer Total Amount': '{:,.0f}',
    'Conversion Rate': '{:.2f}'
}).hide(axis='index')

display(formatted_campaign_performance_sorted)

In [56]:
top_10_campaigns = campaign_performance_sorted.head(10)
top_10_campaigns_cleaned = top_10_campaigns.copy()
top_10_campaigns_cleaned['Campaign'] = top_10_campaigns_cleaned['Campaign'].str[:10]

fig = go.Figure()

fig.add_trace(go.Bar(
    x=top_10_campaigns_cleaned['Campaign'],
    y=top_10_campaigns_cleaned['Total Deals'],
    name='Total Deals',
    marker_color='skyblue'
))

fig.add_trace(go.Bar(
    x=top_10_campaigns_cleaned['Campaign'],
    y=top_10_campaigns_cleaned['Successful Deals'],
    name='Successful Deals',
    marker_color='lightgreen'
))

scaled_conversion_rate = [rate * 40 for rate in top_10_campaigns_cleaned['Conversion Rate']]

fig.add_trace(go.Scatter(
    x=top_10_campaigns_cleaned['Campaign'],
    y=scaled_conversion_rate,
    mode='lines+markers+text',
    name='Conversion Rate (%) (scaled)',
    text=[f'{rate:.1f}%' for rate in top_10_campaigns_cleaned['Conversion Rate']],
    textposition='top center',
    marker=dict(color='red', size=8),
    line=dict(color='red', width=2)
))

fig.update_layout(
    title=dict(
        text='Top 10 Campaigns: Total Deals, Successful Deals, and Conversion Rate',
        x=0.5, xanchor='center'
    ),
    xaxis_title='',
    yaxis_title='Total Deals and Successful Deals',
    yaxis2=dict(title='Conversion Rate (%)', overlaying='y', side='right'),
    legend=dict(x=0.5, y=1.07, xanchor='center', orientation='h'),
    barmode='group',
    xaxis_tickangle=0,
    height=800,
    width=1200
)

fig.show()

####Основные выводы:
- Самая успешная кампания по общему количеству сделок — performancemax_digitalmarkt_ru_DE, но ее конверсия (4.4%) не является самой высокой.  
- Лучшая конверсия (5.5%) у кампании 02.07.23wide_DE, несмотря на меньшее количество сделок.  
- Кампании с высоким числом сделок не всегда демонстрируют высокий коэффициент конверсии, что может указывать на необходимость оптимизации таргетинга или качества лидов.  


Для оценки работы отдела продаж важно понять, какие маркетинговые кампании и источники лидов приносят наибольшую конверсию и прибыль. Для этого мы группируем данные по кампаниям и источникам, рассчитывая среднее и медианное время закрытия сделок, количество и успешность сделок, а также коэффициент конверсии;
оцениваем финансовые показатели, такие как средний чек и общая выручка.

In [57]:
deals_contacts_noTest = deals_contacts[deals_contacts['Source'] != 'Test']
campaign_source_analysis = deals_contacts_noTest.groupby(
    ['Campaign', 'Source']
).agg(
    Mean_Time_to_Close=('Duration', 'mean'),
    Median_Time_to_Close=('Duration', 'median'),
    Total_Deals=('Stage', 'count'),
    Successful_Deals=('Stage', lambda x: (x == 'Payment Done').sum()),
    Conversion_Rate=('Stage', lambda x: (
        (x == 'Payment Done').sum() / len(x) * 100 if len(x) > 0 else 0
    ))
).reset_index()

campaign_detailed_analysis = deals.groupby(
    'Campaign'
).agg(
    Total_Deals=('Stage', 'count'),
    Converted_Deals=('Stage', lambda x: (x == 'Payment Done').sum()),
    Conversion_Rate=('Stage', lambda x: (
        (x == 'Payment Done').sum() / len(x) * 100 if len(x) > 0 else 0
    )),
    Total_Sales=('Initial Amount Paid', 'sum'),
    Avg_Deal_Amount=('Initial Amount Paid', lambda x: x[x > 0].mean()),
    Avg_Time_to_Close=('Closing Date', lambda x: (
        (x - deals.loc[x.index, 'Created Time']).dt.days.mean()
    ))
).reset_index()

stage_distribution_campaign = deals.pivot_table(
    index='Campaign',
    columns='Stage',
    values='Id',
    aggfunc='count',
    fill_value=0
).reset_index()

In [58]:
campaign_source_analysis.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 172 entries, 0 to 171
Data columns (total 7 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   Campaign              172 non-null    object 
 1   Source                172 non-null    object 
 2   Mean_Time_to_Close    172 non-null    float64
 3   Median_Time_to_Close  172 non-null    float64
 4   Total_Deals           172 non-null    int64  
 5   Successful_Deals      172 non-null    int64  
 6   Conversion_Rate       172 non-null    float64
dtypes: float64(3), int64(2), object(2)
memory usage: 9.5+ KB


In [59]:
campaign_source_analysis = deals_contacts_noTest.groupby(
    ['Campaign', 'Source']).agg(
    Mean_Time_to_Close=('Duration', 'mean'),
    Median_Time_to_Close=('Duration', 'median'),
    Total_Deals=('Stage', 'count')).reset_index()
campaign_source_analysis = campaign_source_analysis.merge(
    campaign_performance[['Campaign', 'Successful Deals', 'Conversion Rate']],
    on='Campaign',
    how='left'
)
campaign_source_analysis

Campaign          Source  Mean_Time_to_Close  \
0            01.04.23women_PL    Facebook Ads           12.541667   
1             02.07.23wide_DE    Facebook Ads           25.737069   
2        02.08.23interests_DE    Facebook Ads           13.250000   
3               03.07.23women    Facebook Ads           27.520362   
4    04.07.23recentlymoved_DE    Facebook Ads           21.918330   
..                        ...             ...                 ...   
167              workingin_DE  Telegram posts           19.487179   
168                     yo_DE             SMM           13.100000   
169         youtube_shorts_DE      Google Ads           61.000000   
170         youtube_shorts_DE     Youtube Ads           21.793478   
171       youtube_shortsin_AT     Youtube Ads           12.750000   

     Median_Time_to_Close  Total_Deals  Successful Deals  Conversion Rate  
0                     5.5           24               0.0         0.000000  
1                     6.0          698              52.0         5.531915  
2                     4.5            8               0.0         0.000000  
3                     5.0          442              31.0         5.236486  
4                     5.0          551              31.0         4.258242  
..                    ...          ...               ...              ...  
167                   3.0           39               0.0         0.000000  
168                   4.5           10               0.0         0.000000  
169                  61.0            1              53.0         3.320802  
170                   3.0         1196              53.0         3.320802  
171                   3.5            8               0.0         0.000000  

[172 rows x 7 columns]

In [60]:
campaign_detailed_analysis['Campaign'] = campaign_detailed_analysis['Campaign']\
                                                                    .str[:10]
campaign_source_analysis['Campaign'] = campaign_source_analysis['Campaign']\
                                                                    .str[:10]

fig1 = px.bar(
    campaign_detailed_analysis,
    x='Campaign',
    y='Avg_Deal_Amount',
    labels={'Avg_Deal_Amount': 'Average Deal Amount'},
    color='Avg_Deal_Amount',
    color_continuous_scale='Teal'
)
fig1.update_layout(
    title=dict(
        text="Average Deal Amount by Campaign",
        x=0.5,
        xanchor="center",
        font=dict(size=18)),
    xaxis_title="",
    xaxis=dict(tickangle=-90)
)

fig2 = px.scatter(
    campaign_source_analysis[campaign_source_analysis.Total_Deals > 50],
    x='Campaign',
    y='Mean_Time_to_Close',
    size='Total_Deals',
    color='Conversion Rate',
    hover_name='Source',
    labels={
        'Mean_Time_to_Close': 'Mean Time to Close (days)',
        'Total_Deals': 'Total Deals',
        'Conversion Rate': 'Conversion Rate (%)'
    },
    color_continuous_scale='Viridis',
    size_max=30
)

fig2.update_layout(
    title=dict(
        text="Mean Time to Close by Campaign and Source",
        x=0.5,
        xanchor="center",
        font=dict(size=18)),
    xaxis_title="",
    yaxis_title="Mean Time to Close (days)",
    xaxis=dict(tickangle=-90)
)

fig1.show()
fig2.show()

###  Вывод:  
1. Некоторые кампании приносят значительно больше лидов, чем остальные – их стоит детально анализировать и масштабировать.  
2. Есть кампании с длинным циклом закрытия сделок, что может требовать дополнительных касаний с клиентами.  
3. Высокая конверсия не всегда связана с коротким временем закрытия, что говорит о разных техниках продаж.  
4. Оптимизация кампаний с низкой конверсией и долгими продажами может повысить эффективность маркетинга.  
5. Выявление успешных комбинаций кампаний и источников поможет сфокусироваться на наиболее прибыльных стратегиях.

##Анализ платежей и продуктов:
1. ***Изучите распределение типов оплаты и их влияние на успешность сделок.***


In [61]:
filtered_deals = deals[deals['Payment Type'].astype(str) != 'Unknown']

total_payments = (
    filtered_deals.groupby('Payment Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Total Deals')
)

successful_payments = (
    filtered_deals[filtered_deals['Stage'] == 'Payment Done']
    .groupby('Payment Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals')
)

payment_performance = pd.merge(
    total_payments, successful_payments, on='Payment Type', how='left'
)

payment_performance['Successful Deals'] = (
    payment_performance['Successful Deals'].fillna(0)
)

payment_performance['Conversion Rate'] = (
    payment_performance['Successful Deals']
    / payment_performance['Total Deals'] * 100
).round(1)

fig = px.bar(
    payment_performance,
    x='Payment Type',
    y=['Total Deals', 'Successful Deals'],
    barmode='group',
    color_discrete_map={
        'Total Deals': 'skyblue',
        'Successful Deals': 'lightgreen'
    },
    title='Payment Performance: Total Deals, Successful Deals, '
          'and Conversion Rate',
    text_auto='.2s'
)

for trace in fig.data:
    if 'bar' in trace.type:
        trace.textposition = 'outside'

fig.add_trace(
    go.Scatter(
        x=payment_performance['Payment Type'],
        y=payment_performance['Conversion Rate'],
        mode='lines+markers+text',
        name='Conversion Rate',
        marker=dict(color='red', size=8),
        text=payment_performance['Conversion Rate'].astype(str) + '%',
        textposition='top left'
    )
)

fig.update_layout(
    title_x=0.5,
    yaxis=dict(title='Number of Deals'),
    yaxis2=dict(
        title='Conversion Rate (%)',
        overlaying='y',
        side='right',
        showgrid=False
    ),
    xaxis_title='',
    legend_title='',
    legend=dict(
        orientation="h",
        x=0.5,
        xanchor="center",
        y=1.07
    ),
    height=800,
    width=1200,
    template='plotly_white',
)

fig.show()

### Выводы по графику:
1. Наибольшее количество сделок приходится на категорию Recurring Payments (340 сделок), за ней следует One Payment (140 сделок), а Reservation имеет наименьшее количество сделок (5).
2. Успешные сделки также наиболее сконцентрированы в категории Recurring Payments (250 успешных сделок) и One Payment (110), тогда как у Reservation их всего 1.
3. Коэффициент конверсии:
   - Самый высокий у One Payment – 82.4%, что говорит о высокой вероятности успешного завершения сделок.
   - У Recurring Payments он ниже – 73%, что может свидетельствовать о сложностях в повторных платежах.
   - Самый низкий у Reservation – 20%, что может указывать на высокую вероятность отказа от бронирований.
4. Общий тренд: несмотря на высокое количество сделок у Recurring Payments, их конверсия ниже, чем у One Payment. Это может быть связано с процессом подписки или дополнительными факторами, влияющими на оплату.

 Рекомендация: стоит проанализировать причины более низкой конверсии у Recurring Payments и Reservation — возможно, есть факторы, мешающие успешному завершению сделок.

2. ***Проанализируйте популярность и успешность различных продуктов и типов обучения.***

**Выведем таблицу, показывающую рассчет метрик по типам обучения:**

* количество сделок для каждого типа обучения
* количество успешных сделок для каждого типа обучения
* сумма оплат для успешных сделок по каждому типу обучения (со статусом "Payment Done")
* коэффициент конверсии для каждого типа обучения

In [62]:
filtered_deals = deals[deals['Education Type'].isin(['Morning', 'Evening'])]

education_deals = (
    filtered_deals.groupby('Education Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Total Deals')
)

successful_education_deals = (
    filtered_deals[filtered_deals['Stage'] == 'Payment Done']
    .groupby('Education Type', observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals')
)

total_sales_education = (
    filtered_deals[filtered_deals['Stage'] == 'Payment Done']
    .groupby('Education Type', observed=True)['Offer Total Amount']
    .sum()
    .reset_index()
)

education_performance = pd.merge(
    education_deals, successful_education_deals, on='Education Type', how='left'
)
education_performance = pd.merge(
    education_performance, total_sales_education, on='Education Type', how='left'
)

education_performance[['Successful Deals', 'Offer Total Amount']
                      ] = education_performance[
    ['Successful Deals', 'Offer Total Amount']
].fillna({'Successful Deals': 0, 'Offer Total Amount': 0})

education_performance['Conversion Rate'] = (
    education_performance['Successful Deals'] / \
    education_performance['Total Deals'] * 100
)

education_performance_sorted = education_performance.sort_values(
    by='Successful Deals', ascending=False
)

education_performance_sorted.columns = [
    'Education Type', 'Total Deals', 'Successful Deals',
    'Offer Total Amount', 'Conversion Rate'
]

formatted_education_performance_sorted = education_performance_sorted[
    ['Education Type', 'Total Deals', 'Successful Deals',
     'Offer Total Amount', 'Conversion Rate']
].style.format({
    'Successful Deals': '{:,.0f}',
    'Offer Total Amount': '{:,.0f}',
    'Conversion Rate': '{:.2f}'
}).hide(axis='index')

display(formatted_education_performance_sorted)

**ВЫВОД:** На основе данных таблицы мы можем видеть, что тип обучения "Morning" привлек больше всего сделок (2984) и обеспечил самую высокую сумму продаж (5,713,800), однако его коэффициент конверсии составляет 22.39%. С другой стороны, тип обучения "Evening" показал меньшую общую активность с 406 сделками и суммой продаж 626,30, но при этом продемонстрировал значительно более высокий коэффициент конверсии — 41.87%. Это указывает на то, что вечерние занятия, хотя и менее популярны, имеют более высокую эффективность в преобразовании лидов в успешные сделки.

**Выведем таблицу, показывающую рассчет метрик по продуктам с учетом типов обучения:**
- количество сделок для каждого продукта
- количество успешных сделок для каждого продукта (со статусом "Payment Done")
- сумма оплат для успешных сделок по каждому продукту
- коэффициент конверсии для каждого продукта

In [63]:
product_education_deals = (
    deals.groupby(['Product', 'Education Type'], observed=True)['Id']
    .nunique()
    .reset_index(name='Total Deals')
)

successful_product_education_deals = (
    deals[deals['Stage'] == 'Payment Done']
    .groupby(['Product', 'Education Type'], observed=True)['Id']
    .nunique()
    .reset_index(name='Successful Deals')
)

total_sales_product_education = (
    deals[deals['Stage'] == 'Payment Done']
    .groupby(['Product', 'Education Type'], observed=True)['Offer Total Amount']
    .sum()
    .reset_index()
)

product_education_performance = pd.merge(
    product_education_deals, successful_product_education_deals,
    on=['Product', 'Education Type'], how='left'
)
product_education_performance = pd.merge(
    product_education_performance, total_sales_product_education,
    on=['Product', 'Education Type'], how='left'
)

product_education_performance.fillna(0, inplace=True)

product_education_performance['Conversion Rate'] = (
    product_education_performance['Successful Deals'] /
    product_education_performance['Total Deals'] * 100)

product_education_performance_sorted = product_education_performance.\
sort_values(by='Successful Deals', ascending=False)

formatted_product_education_performance_sorted = (
    product_education_performance_sorted[
        ['Product', 'Education Type', 'Total Deals', 'Successful Deals',
         'Offer Total Amount', 'Conversion Rate']
    ]
    .style.format({
        'Total Deals': '{:,.0f}',
        'Successful Deals': '{:,.0f}',
        'Offer Total Amount': '{:,.0f}',
        'Conversion Rate': '{:.2f}'
    })
    .hide(axis='index')
)

display(formatted_product_education_performance_sorted)

**ВЫВОД:**
- Утренние курсы привлекают больше всего сделок для всех продуктов, при этом курсы по Digital Marketing наиболее популярны и успешны, они имеют 1618 сделок, из которых 361 были успешными, что привело к общей сумме продаж в 3,522,200 и коэффициенту конверсии 22.31%.
- Вечерние курсы по Digital Marketing также показывают высокий коэффициент конверсии (44.66%) при 253 сделки и 113 успешных.
- UX/UI Design и Web Developer курсы также популярны в утренние часы, с 815 и 542 сделками соответственно, и успешными сделками в 170 и 137.
- Вечерние курсы по UX/UI Design имеют высокий коэффициент конверсии (37.50%) с 152 сделками и 57 успешными.

In [64]:
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=("Product Performance by Education Type",
                    "Revenue Share by Product and Education Type"),
    specs=[[{"type": "xy"}, {"type": "domain"}]]
)

soft_colors_total = px.colors.qualitative.Pastel
soft_colors_successful = px.colors.qualitative.Pastel2
soft_colors_pie = px.colors.qualitative.Set3

fig_bar = px.bar(
    product_education_performance_sorted,
    x="Product",
    y="Total Deals",
    color="Education Type",
    text_auto=True,
    barmode="stack",
    color_discrete_sequence=soft_colors_total
)

threshold = 10
fig_bar2 = px.bar(
    product_education_performance_sorted,
    x="Product",
    y="Successful Deals",
    color="Education Type",
    barmode="stack",
    color_discrete_sequence=soft_colors_successful
)

for trace in fig_bar2.data:
    trace.text = [
        f"{y:.0f}" if y > threshold else ""
        for y in trace.y
    ]
    trace.textposition = "inside"

for trace in fig_bar.data:
    fig.add_trace(trace, row=1, col=1)
for trace in fig_bar2.data:
    fig.add_trace(trace, row=1, col=1)

pie_data = product_education_performance_sorted.groupby(
    ["Product", "Education Type"]
)["Offer Total Amount"].sum().reset_index()

fig_pie = px.pie(
    pie_data,
    values="Offer Total Amount",
    color = 'Product',
    names=[f"{prod} ({edu})" for prod, edu in zip(pie_data["Product"],
                                                  pie_data["Education Type"])],
    color_discrete_sequence = soft_colors_pie
)

for trace in fig_pie.data:
    fig.add_trace(trace, row=1, col=2)

fig.update_layout(
    height=500, width=1100,
    showlegend=True,
    template="plotly_white"
)

fig.show()

### Краткие выводы по графикам:

1. Гистограмма:  
   - Digital Marketing имеет наибольшее число сделок, особенно в утреннем формате.  
   - UX/UI Design занимает второе место, с явным перевесом утренних сделок.  
   - Web Developer показывает наименьшее количество сделок, особенно в вечернее время.  
   - В целом, утренний формат более популярен во всех продуктах.

2. Круговая диаграмма:
   - Основной вклад в доход приносит Digital Marketing (Morning) – 55.6%.  
   - UX/UI Design (Morning) также занимает значительную долю – 25.4%.  
   - Вечерние программы (особенно Web Developer Evening) приносят минимальный доход.  
   - Вклад Web Developer (Morning) и Digital Marketing (Evening) невелик по сравнению с лидерами.  

### Общий вывод:
- Утренние программы значительно более востребованы и приносят больше дохода.
- Digital Marketing (Morning) – лидер как по числу сделок, так и по финансовому вкладу.  
- Вечерние программы требуют пересмотра стратегии из-за низкой популярности и доходности.

 ## Географический анализ:
1. ***Проанализируйте географическое распределение сделок по городам.***



In [65]:
with open("city_data_google.json", "r") as json_file:
    city_data = json.load(json_file)

In [66]:
def get_city_info(city):
    info = city_data.get(city, {})
    return pd.Series({
        'longitude': info.get('longitude', None),
        'latitude': info.get('latitude', None),
        'country_ru': info.get('country', None),
        'city_ru': info.get('formatted_address', None)
    })

deals['City'] = deals['City'].fillna('Unknown')
deals[['longitude', 'latitude', 'country_ru', 'city_ru']
      ] = deals['City'].apply(get_city_info)

In [67]:
deals.loc[deals.City != "Unknown"].head()

Id  Deal Owner Name Closing Date  Quality  \
32  5805028000056714532    Ulysses Adams          NaT      NaN   
39  5805028000056731279    Ulysses Adams          NaT      NaN   
49  5805028000056683030    Charlie Davis          NaT  C - Low   
50  5805028000056568397  Paula Underwood          NaT      NaN   
53  5805028000056558351    Ulysses Adams          NaT  C - Low   

                    Stage Lost Reason       Page               Campaign  \
32  Registered on Webinar         NaN   /webinar            webinar1906   
39  Registered on Webinar         NaN   /webinar                    NaN   
49    Waiting For Payment         NaN  /eng/test  performancemax_eng_DE   
50  Registered on Webinar         NaN   /webinar                    NaN   
53    Waiting For Payment         NaN       /eng                    NaN   

            Content        Term  ... Initial Amount Paid Offer Total Amount  \
32              NaN  invitation  ...                 NaN                NaN   
39              NaN         NaN  ...                 NaN                NaN   
49  _{region_name}_         NaN  ...              1000.0             9000.0   
50              NaN         NaN  ...                 NaN                NaN   
53              NaN         NaN  ...              1000.0             9000.0   

           Contact Name        City Level of Deutsch  SLA Seconds  longitude  \
32  5805028000044019127      Berlin          Unknown          NaN  13.404954   
39  5805028000054755989   Lahnstein          Unknown          NaN   7.609363   
49  5805028000056690015  Crailsheim          Unknown       1239.0  10.063357   
50  5805028000020664131    Prenzlau               B1          NaN  13.862376   
53  5805028000056578244    Dortmund               B1        589.0   7.465298   

     latitude  country_ru      city_ru  
32  52.520007    Германия       Берлин  
39  50.307827    Германия     Ланштайн  
49  49.133735    Германия  Крайльсхайм  
50  53.316844    Германия     Пренцлау  
53  51.513587    Германия     Дортмунд  

[5 rows x 27 columns]

In [68]:
deals['City'] = deals.City.replace('-', "Unknown")

In [69]:
deals.to_csv("deals_geo.csv", index=False)

Подсчет статистик

In [70]:
geo_deals = deals[['Id', 'City']]
geo_deals_clean = geo_deals.dropna(subset=['City'])
deals_by_city = geo_deals_clean.groupby('City')\
  .size().reset_index(name='Number of Deals')

deals_by_city_sorted = deals_by_city.sort_values(
    by='Number of Deals', ascending=False)
deals_by_city_sorted

City  Number of Deals
774               Unknown            17096
88                 Berlin              264
521               München               88
288               Hamburg               78
570              Nürnberg               53
..                    ...              ...
442  Liederbach am Taunus                1
443            Lierschied                1
444    Limbach-Oberfrohna                1
448                  Linz                1
870                  Śrem                1

[871 rows x 2 columns]

In [71]:
geo_data_deals = deals[["City", "longitude", "latitude", "country_ru",
                           "city_ru"]].drop_duplicates(subset=["City"]).dropna()

In [72]:
deals_by_city_sorted = deals_by_city_sorted.merge(
    geo_data_deals, on='City', how="inner")
deals_by_city_sorted

City  Number of Deals  longitude   latitude country_ru  \
0                  Berlin              264  13.404954  52.520007   Германия   
1                 München               88  11.581981  48.135125   Германия   
2                 Hamburg               78   9.987170  53.548828   Германия   
3                Nürnberg               53  11.074564  49.454288   Германия   
4                 Leipzig               52  12.373075  51.339695   Германия   
..                    ...              ...        ...        ...        ...   
864  Liederbach am Taunus                1   8.484905  50.127530   Германия   
865            Lierschied                1   7.746058  50.170155   Германия   
866    Limbach-Oberfrohna                1  12.753720  50.857566   Германия   
867                  Linz                1  14.285918  48.306910    Австрия   
868                  Śrem                1  17.015060  52.088700     Польша   

              city_ru  
0              Берлин  
1              Мюнхен  
2             Гамбург  
3            Нюрнберг  
4             Лейпциг  
..                ...  
864          Лидербах  
865            Лиршид  
866  Лимбах-Оберфрона  
867              Линц  
868             Сьрем  

[869 rows x 6 columns]

In [73]:
bar_color = px.colors.qualitative.Pastel[0]

fig = go.Figure(data=[
    go.Bar(
        name='Number of Deals',
        x=deals_by_city_sorted['City'].head(10),
        y=deals_by_city_sorted['Number of Deals'].head(10),
        marker_color=bar_color
    )
])

fig.update_layout(
    title=dict(text="Top 10 Cities by Number of Deals", x=0.5),
    yaxis_title="Number of Deals",
    xaxis_tickangle=0
)

fig.show()

In [74]:
deals_by_city_sorted.to_csv("deals_by_city_sorted.csv", index=False)

In [75]:
deals_geo = deals[deals['City'] != 'Unnamed'].dropna(subset="city_ru")

geometry = [Point(xy) for xy in zip(deals_geo["longitude"],
                                    deals_geo["latitude"])]

gdf = gpd.GeoDataFrame(deals_geo, geometry=geometry)

gdf.set_crs(epsg=4326, inplace=True)

display(gdf.head())

Id  Deal Owner Name Closing Date  Quality  \
32  5805028000056714532    Ulysses Adams          NaT      NaN   
39  5805028000056731279    Ulysses Adams          NaT      NaN   
49  5805028000056683030    Charlie Davis          NaT  C - Low   
50  5805028000056568397  Paula Underwood          NaT      NaN   
53  5805028000056558351    Ulysses Adams          NaT  C - Low   

                    Stage Lost Reason       Page               Campaign  \
32  Registered on Webinar         NaN   /webinar            webinar1906   
39  Registered on Webinar         NaN   /webinar                    NaN   
49    Waiting For Payment         NaN  /eng/test  performancemax_eng_DE   
50  Registered on Webinar         NaN   /webinar                    NaN   
53    Waiting For Payment         NaN       /eng                    NaN   

            Content        Term  ... Offer Total Amount         Contact Name  \
32              NaN  invitation  ...                NaN  5805028000044019127   
39              NaN         NaN  ...                NaN  5805028000054755989   
49  _{region_name}_         NaN  ...             9000.0  5805028000056690015   
50              NaN         NaN  ...                NaN  5805028000020664131   
53              NaN         NaN  ...             9000.0  5805028000056578244   

          City Level of Deutsch SLA Seconds  longitude   latitude  country_ru  \
32      Berlin          Unknown         NaN  13.404954  52.520007    Германия   
39   Lahnstein          Unknown         NaN   7.609363  50.307827    Германия   
49  Crailsheim          Unknown      1239.0  10.063357  49.133735    Германия   
50    Prenzlau               B1         NaN  13.862376  53.316844    Германия   
53    Dortmund               B1       589.0   7.465298  51.513587    Германия   

        city_ru                   geometry  
32       Берлин  POINT (13.40495 52.52001)  
39     Ланштайн   POINT (7.60936 50.30783)  
49  Крайльсхайм  POINT (10.06336 49.13374)  
50     Пренцлау  POINT (13.86238 53.31684)  
53     Дортмунд    POINT (7.4653 51.51359)  

[5 rows x 28 columns]

In [76]:
gdf.geometry.is_empty.sum()

0

In [77]:
center = gdf.geometry.union_all().centroid
m = folium.Map(location=[center.y, center.x], zoom_start=4)

marker_cluster = MarkerCluster().add_to(m)

for _, row in gdf.iterrows():
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        popup=f"Index: {_}"
    ).add_to(marker_cluster)

m.save("deals_map_cluster.html")
m

####Выводы из анализа географических данных по городам и странам.

1. Географическое распределение сделок
* Наибольшее количество сделок сосредоточено в Центральной Европе, в частности в Германии, что подтверждается кластеризацией точек на карте.
* Берлин является абсолютным лидером по количеству сделок, что также подтверждается диаграммой топ-10 городов.
* Помимо Германии, сделки активно заключаются в Восточной Европе, Ближнем Востоке и Северной Америке.
* Наименьшее количество сделок зафиксировано в Северной Америке и некоторых регионах Азии. На карте они представлены одиночными синими точками.

2. Лидирующие города по количеству сделок
* Топ-3 города по количеству сделок:
 1. Берлин – с большим отрывом занимает первое место.
 2. Мюнхен и Гамбург – находятся на втором и третьем местах соответственно, но с заметно меньшими объемами сделок.
* Остальные города в рейтинге (Нюрнберг, Лейпциг, Дюссельдорф, Франкфурт, Дрезден, Дортмунд, Кёльн) имеют значительно меньше сделок, что подтверждает концентрацию бизнеса в нескольких крупнейших экономических центрах.

3. Общие выводы
* Рынок сделок сильно сконцентрирован в Германии, особенно в таких городах, как Берлин, Мюнхен и Гамбург.
* Восточная Европа и Ближний Восток показывают умеренную активность, но отстают по числу сделок.
* Разброс сделок в США и других странах минимален, что может указывать либо на недостаточную представленность бизнеса в этих регионах, либо на низкий спрос.

Рекомендации:

* Если целью является расширение рынка, стоит обратить внимание на развитие продаж в соседних странах Европы и странах Ближнего Востока.
* Проведение анализов спроса в США поможет понять, почему сделки там менее активны.
* В Германии можно укреплять присутствие в других городах, кроме Берлина, где уже и так максимальная концентрация сделок.

Заключение:  
Анализ показывает четкую географическую концентрацию сделок в Центральной Европе (в основном Германии), а также перспективные рынки для развития в Восточной Европе и Ближнем Востоке

2. ***Изучите влияние уровня знания немецкого языка на успешность сделок в разных городах.***

Используем Payment Done как признак успешных сделок:

In [78]:
filtered_deals = deals.dropna(subset=['City', 'Level of Deutsch'])

deals_by_city_lang = (
    filtered_deals.groupby(['City', 'Level of Deutsch'])
    .agg(Total_Deals=('Id', 'count'),
         Successful_Deals=('Stage', lambda x: (x == 'Payment Done').sum()))
    .reset_index()
)

deals_by_city_lang['Success_Rate'] = (
    deals_by_city_lang['Successful_Deals'] / deals_by_city_lang['Total_Deals']
) * 100

print(deals_by_city_lang.head())
print(deals_by_city_lang["Success_Rate"].describe())

        City Level of Deutsch  Total_Deals  Successful_Deals  Success_Rate
0     Aachen               A2            1                 0           0.0
1     Aachen               B1            5                 2          40.0
2     Aachen          Unknown            4                 1          25.0
3      Aalen          Unknown            3                 0           0.0
4  Abensberg          Unknown            1                 0           0.0
count    1188.000000
mean       28.279459
std        39.878991
min         0.000000
25%         0.000000
50%         0.000000
75%        50.000000
max       100.000000
Name: Success_Rate, dtype: float64


In [79]:
deals_by_city_lang_filtered = deals_by_city_lang[
    (deals_by_city_lang['Level of Deutsch'] != "Unknown") &
    (deals_by_city_lang["City"] != "Unknown")
]

top_cities = deals_by_city_lang_filtered.groupby("City")["Total_Deals"]\
.sum().nlargest(10).index
deals_top_cities = deals_by_city_lang_filtered[
    deals_by_city_lang_filtered["City"].isin(top_cities)]

fig = px.bar(
    deals_top_cities,
    x="City",
    y="Success_Rate",
    color="Level of Deutsch",
    title="Success Rate by City and Level of German Language (Top 10 Cities)",
    labels={"Success_Rate": "Success Rate (%)", "City": "City",
            "Level of Deutsch": ""},
    barmode="group",
    text_auto=".2f"
)

fig.update_layout(
    title_x=0.5,
    legend=dict(
    orientation="h",
    yanchor="bottom",
    y=1.02,
    xanchor="center",
    x=0.5,
    title_text=""
    )
)

fig.show()

####Вывод по графику:
1. Высокий уровень успешности среди носителей C1 и B2 – в некоторых городах (например, Duisburg и Köln) видно, что уровень C1 показывает 100% успеха, а B2 стабильно высокие показатели.
2. Разброс успешности по уровням – в разных городах уровень успешности варьируется. Например, в München, Leipzig и Köln высокие показатели у уровней A2, B1 и B2.
3. Города-лидеры по успеху – Duisburg и Hamburg выделяются высокой успешностью определенных уровней языка.
4. Города с равномерным распределением – в Berlin и Leipzig успех распределен относительно равномерно между всеми уровнями.
5. Возможная зависимость от города – города с высоким уровнем немецкого (B2 и C1) демонстрируют лучшие результаты, что может указывать на важность языковой подготовки в успехе сделок.